In [1]:
from pyspark import SparkConf, SparkContext
import pyspark

# mapper1
* 形成 (節點, (out-link, r/d) 的形式
* 同時加上 (節點, (節點, 0.0))，避免沒有out的點不見

In [2]:
def mapper1(line):
    maplist = []
    maplist.append((line[0], (line[0], 0.0)))
    d = len(line[1])-1
    for i in range(d):
        maplist.append((line[0], (line[1][i], line[1][-1]/d)))
        
    return maplist

# mapper2
* 形成 (節點, [接收到的每個in-link值]) 的形式

In [3]:
def mapper2(line):
    maplist = []    
    for i in range(len(line[1])):  
        maplist.append((line[1][i][0], line[1][i][1]))
    
    return maplist

In [4]:
def reducer(x, y):
    return x + y

# adder
* 算出in-link值總和為我多少，在求出r值
* 形成 (節點, r) 的形式

In [5]:
def adder(line):
    maplist = []
    val = 0
    for i in line[1]:
        val += i
    val = 0.8*val + 0.2/10876
    maplist.append((line[0], val))
    
    return maplist

# accu
* 用來加總S的值

In [6]:
def accu(x): 
   global num
   num += x   

* 先把data整理成 (節點, [所有out-link, r值]) 的形式

In [8]:
conf = SparkConf().set("spark.default.parallelism", 4).setAppName("PageRank")
sc = SparkContext.getOrCreate(conf=conf)
lines = sc.textFile("p2p-Gnutella04.txt").map(lambda v: v.split('\t')).map(lambda v: (v[0], v[1])).groupByKey().mapValues(list)
r = sc.textFile("p2p-Gnutella04.txt").map(lambda v: v.split('\t')).map(lambda v: (v[0], [1/10876])).reduceByKey(lambda x, y: x).mapValues(list)
lines1 = lines.union(r).reduceByKey(lambda x, y: x + y)
print(lines1.collect())

[('0', ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', 9.194556822361162e-05]), ('1', ['2', '11', '12', '13', '14', '15', '16', '17', '18', '19', 9.194556822361162e-05]), ('8', ['30', '31', '32', '33', '34', '35', '36', '37', '38', '39', 9.194556822361162e-05]), ('10', ['41', '136', '137', '138', '139', '140', '141', '142', '143', '144', 9.194556822361162e-05]), ('12', ['40', '41', '42', '43', '44', '45', '46', '47', '48', '49', 9.194556822361162e-05]), ('14', ['199', '756', '1116', '2537', '2787', '3307', '4524', '4674', '6016', '7040', 9.194556822361162e-05]), ('17', ['79', '80', '81', '82', '83', '84', '85', '86', '87', '88', 9.194556822361162e-05]), ('19', ['69', '70', '71', '72', '73', '74', '75', '76', '77', '78', 9.194556822361162e-05]), ('20', ['50', '51', '52', '53', '54', '55', '56', '57', '58', '59', 9.194556822361162e-05]), ('21', ['22', '60', '61', '62', '63', '64', '65', '66', '67', '68', 9.194556822361162e-05]), ('26', ['78', '89', '90', '91', '92', '93', '94', '95',

* mapper1回傳後，用gourpByKey找出相同key的value，形成list

In [9]:
lines2 = lines1.flatMap(mapper1).groupByKey().mapValues(list)
print(lines2.collect())

[('0', [('0', 0.0), ('1', 9.194556822361162e-06), ('2', 9.194556822361162e-06), ('3', 9.194556822361162e-06), ('4', 9.194556822361162e-06), ('5', 9.194556822361162e-06), ('6', 9.194556822361162e-06), ('7', 9.194556822361162e-06), ('8', 9.194556822361162e-06), ('9', 9.194556822361162e-06), ('10', 9.194556822361162e-06)]), ('1', [('1', 0.0), ('2', 9.194556822361162e-06), ('11', 9.194556822361162e-06), ('12', 9.194556822361162e-06), ('13', 9.194556822361162e-06), ('14', 9.194556822361162e-06), ('15', 9.194556822361162e-06), ('16', 9.194556822361162e-06), ('17', 9.194556822361162e-06), ('18', 9.194556822361162e-06), ('19', 9.194556822361162e-06)]), ('8', [('8', 0.0), ('30', 9.194556822361162e-06), ('31', 9.194556822361162e-06), ('32', 9.194556822361162e-06), ('33', 9.194556822361162e-06), ('34', 9.194556822361162e-06), ('35', 9.194556822361162e-06), ('36', 9.194556822361162e-06), ('37', 9.194556822361162e-06), ('38', 9.194556822361162e-06), ('39', 9.194556822361162e-06)]), ('10', [('10', 0

* mapper2回傳後，用gourpByKey找出相同key的value，形成list

In [10]:
lines3 = lines2.flatMap(mapper2).groupByKey().mapValues(list)
print(lines3.collect())

[('0', [0.0, 1.5324261370601937e-05, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06]), ('1', [9.194556822361162e-06, 0.0, 4.839240432821665e-06, 9.194556822361162e-06, 9.194556822361162e-06]), ('4', [9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 5.7465980139757265e-06, 9.194556822361162e-05, 9.194556822361162e-06, 4.597278411180581e-05, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 4.597278411180581e-05]), ('8', [9.194556822361162e-06, 0.0]), ('9', [9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 1.0216174247067958e-05, 9.194556822361162e-06, 9.194556822361162e-06, 3.2837702937004153e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162e-06, 9.194556822361162

In [11]:
lines4 = lines3.flatMap(adder)
print(lines4.collect())

[('0', 7.478239548853746e-05), ('1', 4.432744236464645e-05), ('4', 0.0002583670467083487), ('8', 2.5744759102611254e-05), ('9', 0.00013952375114567096), ('10', 5.046790078051571e-05), ('12', 3.3100404560500183e-05), ('14', 4.127334395815456e-05), ('16', 8.458992276572269e-05), ('17', 5.5984634873932415e-05), ('19', 4.781169547627804e-05), ('33', 0.00018429978341710597), ('34', 6.334028033182134e-05), ('138', 6.334028033182134e-05), ('139', 3.493931592497242e-05), ('140', 0.00016002134579466213), ('141', 7.151321972947571e-05), ('143', 5.131438378955849e-05), ('144', 2.5744759102611254e-05), ('40', 5.5167340934166975e-05), ('44', 0.0001446610273384823), ('45', 6.987863184994484e-05), ('48', 8.642883413019492e-05), ('756', 0.00013086919210494055), ('2537', 4.781169547627804e-05), ('3307', 8.622451064525357e-05), ('82', 2.5744759102611254e-05), ('83', 0.00011401250459727842), ('84', 4.781169547627804e-05), ('86', 7.069592578971027e-05), ('88', 4.0456050018389116e-05), ('69', 0.00014506967

* 使用accumulator來加總S的值

In [12]:
num = sc.accumulator(0.0)
lines4.values().foreach(accu)
global S
S = num.value
print(S)

0.5630011033468121


* 形成 (節點, r_new) 的形式

In [13]:
lines5 = lines4.map(lambda x: (x[0], [x[1]+(1-S)/10876]))
print(lines5.collect())

[('0', [0.00011496250735440616]), ('1', [8.450755423051514e-05]), ('4', [0.00029854715857421737]), ('8', [6.592487096847994e-05]), ('9', [0.00017970386301153964]), ('10', [9.06480126463844e-05]), ('12', [7.328051642636888e-05]), ('14', [8.145345582402324e-05]), ('16', [0.0001247700346315914]), ('17', [9.616474673980111e-05]), ('19', [8.799180734214674e-05]), ('33', [0.00022447989528297466]), ('34', [0.00010352039219769003]), ('138', [0.00010352039219769003]), ('139', [7.511942779084112e-05]), ('140', [0.00020020145766053081]), ('141', [0.00011169333159534439]), ('143', [9.149449565542717e-05]), ('144', [6.592487096847994e-05]), ('40', [9.534745280003566e-05]), ('44', [0.000184841139204351]), ('45', [0.00011005874371581353]), ('48', [0.0001266089459960636]), ('756', [0.00017104930397080924]), ('2537', [8.799180734214674e-05]), ('3307', [0.00012640462251112226]), ('82', [6.592487096847994e-05]), ('83', [0.00015419261646314712]), ('84', [8.799180734214674e-05]), ('86', [0.0001108760376555

* 前面做過1次，所以再做19次

In [14]:
for i in range(19):
    lines1 = lines.union(lines5).reduceByKey(lambda x, y: x + y)
    lines2 = lines1.flatMap(mapper1).groupByKey().mapValues(list)
    lines3 = lines2.flatMap(mapper2).groupByKey().mapValues(list)
    lines4 = lines3.flatMap(adder)
    num = sc.accumulator(0.0)
    lines4.values().foreach(accu)
    S = num.value
    lines5 = lines4.map(lambda x: (x[0], [x[1]+(1-S)/10876]))

In [15]:
print(lines5.collect())

[('88', [0.00011060022097330707]), ('180', [0.00016820599019298085]), ('285', [8.325298543815719e-05]), ('356', [0.000138203921672543]), ('465', [7.37823199544307e-05]), ('586', [6.389142920319501e-05]), ('671', [7.324160327482659e-05]), ('683', [9.274429465792517e-05]), ('831', [6.768136719150338e-05]), ('990', [8.649244995376814e-05]), ('1025', [0.00013487334449929208]), ('1112', [9.330547686759266e-05]), ('1863', [0.0002275485816873124]), ('1243', [0.00014590900239231467]), ('3227', [9.391461180483364e-05]), ('1392', [8.332736213076581e-05]), ('3478', [0.00010033549994118194]), ('1564', [9.649119011195537e-05]), ('1572', [7.055518881100194e-05]), ('1655', [9.928604844262583e-05]), ('3649', [0.00010643580891824068]), ('1764', [0.00016294204031087184]), ('4012', [7.721632368979324e-05]), ('1820', [0.00010669246253184404]), ('1846', [0.00010833517133457753]), ('2017', [0.00011055762007305118]), ('2085', [8.402891145439846e-05]), ('2111', [7.583559176032979e-05]), ('2394', [0.0001070617

* 把key跟value的位置對調，然後sort

In [17]:
result = lines5.map(lambda x: (x[1][0], x[0]))
sort = sorted(result.collect(), reverse = True)
print(sort)

[(0.0006321988095901942, '1056'), (0.0006291557128603987, '1054'), (0.0005239103397527083, '1536'), (0.0005116224706020384, '171'), (0.0004956586476699695, '453'), (0.00048484419963902656, '407'), (0.000479619289318484, '263'), (0.0004704975514074375, '4664'), (0.0004628915865689017, '261'), (0.0004615100382904273, '410'), (0.0004605290905057315, '1959'), (0.0004597276674070256, '165'), (0.0004405185787770371, '1198'), (0.0004283493544637901, '127'), (0.0004195080597913252, '4054'), (0.0004105298711967811, '2265'), (0.0004103613358523226, '345'), (0.00040913967043426343, '763'), (0.00040040758959259103, '989'), (0.0003994790670464678, '987'), (0.00039532479790330556, '408'), (0.00038993089781126747, '329'), (0.0003836148669501645, '4'), (0.00037964439230214037, '1551'), (0.0003793468078045828, '699'), (0.000377443724240052, '982'), (0.0003762153461537934, '903'), (0.00037610885737022646, '481'), (0.00037508959877272395, '2485'), (0.0003740926146024567, '1055'), (0.0003721772591593169, 

* 印出前十大的pagerank
* 四捨五入取到小數點後第10位

In [18]:
for i in range(10):
    print('{:6}'.format(str(sort[i][1])) + str(round(sort[i][0], 10)))

1056  0.0006321988
1054  0.0006291557
1536  0.0005239103
171   0.0005116225
453   0.0004956586
407   0.0004848442
263   0.0004796193
4664  0.0004704976
261   0.0004628916
410   0.00046151


* 寫入Output.txt

In [21]:
with open('Outputfile.txt', 'w') as f:
    for i in range(10):
        f.write('{:6}'.format(str(sort[i][1])) + str(round(sort[i][0], 10)) + '\n')

In [22]:
sc.stop()